# VDF Function Search For edges

In order to apply any system optimal route assignment algorithms, volume delay functions for each edge in the graph has to be defined. This will be estimated from volume travel time pairs recorded from 4 simulations runs, each with 20 iterations. The travel volume was scaled from 10% to 100% at a step of 10% per iteration, so the the final 10 iterations of each run are all at 100% volume.

In [11]:
import qgrid
import pandas as pd
import numpy as np
from ipywidgets import interact, interact_manual
import ipywidgets as widgets
from IPython.display import display, clear_output, Image
from typing import Tuple, Sequence

from os import path
import pickle

# Standard plotly imports
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
# Using plotly + cufflinks in offline mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

## Load and display the data

In [2]:
def read_edge_vol_delay(in_files: Sequence[str]) -> pd.DataFrame:
    # import here to not polute the notebook namespace
    from EdgeRouteParser import dynamic_assignment_file_read, timevol_table, functions_expansion
    import pathos.multiprocessing as mp
    
    in_files = [file for file in in_files if '_' in path.split(file)[-1]]
    with mp.Pool() as pool:
        tables = pool.map(functions_expansion(dynamic_assignment_file_read,
                                              lambda tbd: tbd['VolTime'],
                                              timevol_table
                                              ), in_files)

    sim_itr = [int(path.basename(fr).split('.')[0].split('_')[-1])
               for fr in in_files]
    sim_dem = [float(path.split(path.split(fr)[0])[-1]
                     .replace('Vol', '').replace('per', '')) / 100 for fr in in_files]
    for itr, dem, table in zip(sim_itr, sim_dem, tables):
        table['ITR'] = itr
        table['Demand'] = dem

    return pd.concat(tables)

In [3]:
# load from cache if exists
try:
    edge_volume_time = pd.read_pickle("edge_volume_time.pkl.gz")
except FileNotFoundError:
    from EdgeRouteParser import files_by_ext
    files = files_by_ext(path.abspath(r"..\Urban Freeway Dyn Assign Redmond.US"), 'bew')
    files = [file for file in files if '_' in path.split(file)[-1]]
    edge_volume_time = read_edge_vol_delay(files)
    edge_volume_time = edge_volume_time.rename(index=str, columns={"NO": "Edge", "TRAVTMNEW": "TravelTime", "VOLNEW": 'Volume'})
    edge_volume_time.to_pickle("edge_volume_time.pkl.gz", compression="gzip")
    del files

### Simulation results

|     NO     |   VehType    |              Period                         |        TravelTime         |       Volume        | ITR                  | Demand |
|:----------:|:------------:|:-------------------------------------------:|:------------------------:|:------------------:|:---------------------:|:------:|
|edge number | vehicle type | simulation data sample period (10 min each) | average edge travel time | 10 min volume count | simulation iteration | DTA demand proportion |


In [4]:
qgrid.show_grid(edge_volume_time, grid_options={'editable': False,'maxVisibleRows':8})

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

## Create interactive travel time vs 15 min volume plot

In [5]:
def VD_data_filter(edge=75,
                   veh_type=list(edge_volume_time['VehType'].unique())[0],
                   itr=(edge_volume_time['ITR'].min(),
                        edge_volume_time['ITR'].max()),
                   period=(edge_volume_time['Period'].min(),
                           edge_volume_time['Period'].max()),
                   demand=(edge_volume_time['Demand'].min(),
                           edge_volume_time['Demand'].max())):

    # Filter for plotting
    filtered_frame = edge_volume_time[(edge_volume_time['Edge'] == edge) &
                                      (edge_volume_time['VehType'] == veh_type) &
                                      (edge_volume_time['ITR'] >= itr[0]) &
                                      (edge_volume_time['ITR'] <= itr[1]) & 
                                      (edge_volume_time['Period'] >= period[0]) &
                                      (edge_volume_time['Period'] <= period[1]) & 
                                      (edge_volume_time['Demand'] >= demand[0]) &
                                      (edge_volume_time['Demand'] <= demand[1])]


    return filtered_frame

In [25]:
# function to turn dataframe to plotly plot
def edge_VD_plot(*args, **kwargs) -> dict:
    plotting_frame = VD_data_filter(*args, **kwargs)

    def row_2_text(row):
        row = row[1]
        return "Vol: {}, Time: {:.2f}s<br>".format(row.Volume, row.TravelTime) + \
               "Itr: {}, Period: {}<br>".format(row.ITR, row.Period) + \
               "Demand: {}".format(row.Demand)
    text = [row_2_text(row) for row in plotting_frame.iterrows()]

    # get different iteration series for plotly
    return dict(
        x=plotting_frame.Volume.to_numpy(),
        y=plotting_frame.TravelTime.to_numpy(),
        mode='markers',
        text=text,
        hoverinfo='text',
        marker=dict(
            color=plotting_frame.Demand.to_numpy(),
            colorbar=dict(title='Sim Demand'),
            colorscale='Portland',
            reversescale=False
        ),
    )


# Build widgets
style = {'description_width': 'initial'}
layout = widgets.Layout(width='95%')
edge_wig = widgets.IntSlider(min=edge_volume_time['Edge'].min(),
                             max=edge_volume_time['Edge'].max(),
                             step=1,
                             description='Network Edge:',
                             value=75,
                             style=style,
                             layout=layout,
                             continuous_update=False)

veh_type_wig = widgets.Dropdown(options=list(edge_volume_time['VehType'].unique()),
                                description='Vehicle Type:',
                                value=list(
                                    edge_volume_time['VehType'].unique())[0],
                                style=style)

ITR_wig = widgets.IntRangeSlider(min=edge_volume_time['ITR'].min(),
                                 max=edge_volume_time['ITR'].max(),
                                 step=1,
                                 value=(5, 20),
                                 description='Sim Iteration:',
                                 style=style,
                                 layout=layout,
                                 continuous_update=False)

Period_wig = widgets.IntRangeSlider(min=edge_volume_time['Period'].min(),
                                 max=edge_volume_time['Period'].max(),
                                 step=1,
                                 value=(2, 6),
                                 description='DTA Period:',
                                 style=style,
                                 layout=layout,
                                 continuous_update=False)

Demand_wig = widgets.FloatRangeSlider(min=edge_volume_time['Demand'].min()-0.1,
                                 max=edge_volume_time['Demand'].max()+0.1,
                                 step=0.1,
                                 description='DTA Traffic Demand:',
                                 style=style,
                                 layout=layout,
                                      readout_format='.0%',
                                 continuous_update=False)



# drop_first_last_wig = widgets.Checkbox(
#     value=True,
#     description='Drop first and last sim period',
#     style=style,
# )

input_wigs = [edge_wig, veh_type_wig, ITR_wig, Period_wig, Demand_wig]

# Create interactive plot
plt_layout = {
    'xaxis': {'title': '10 min Volume (count)', 'rangemode': 'tozero'},
    'yaxis': {'title': "Average Vehicle Travel Time (s)", 'rangemode': 'tozero'},
    'autosize': True,
    'hovermode': 'closest',
    'plot_bgcolor': 'white'
    # 'template': 'plotly_dark'
}

plot_fig = go.FigureWidget(data=[go.Scatter(**edge_VD_plot(*[wig.value for wig in input_wigs]))],
                           layout=plt_layout)

def update_plot(_):
    with plot_fig.batch_update():
        updated_data = edge_VD_plot(*[wig.value for wig in input_wigs])
        plot_fig.data[0].x = updated_data['x']
        plot_fig.data[0].y = updated_data['y']
        plot_fig.data[0].text = updated_data['text']
        plot_fig.data[0].marker = updated_data['marker']

[wig.observe(update_plot, names="value") for wig in input_wigs]

out = widgets.VBox(input_wigs + [plot_fig], layout=widgets.Layout(width='100%'))
display(out)


# Testing Volume Delay estimators

In [7]:
# read edge attributes from disk

edge_attr = pd.read_pickle("edges_attr.pkl.gz")

## Edge free flow travel time

In order to anchor any volume delay function to free flow conditions, the mean free flow travel time is required. 

Using the  interactive plot from above, the travel time at 10%-30% traffic demand, during sim period 2 to 6, and after iteration 15 appear to be good data points to estimate free flow time.

In [8]:
all_FF_time: pd.DataFrame
all_FF_time = edge_volume_time[(edge_volume_time['VehType'] == 'ALL') &
                               (edge_volume_time['ITR'] >= 15) &
                               (edge_volume_time['ITR'] <= 20) &
                               (edge_volume_time['Period'] >= 2) &
                               (edge_volume_time['Period'] <= 6) &
                               (edge_volume_time['Demand'] >= 0.1) &
                               (edge_volume_time['Demand'] <= 0.3) &
                               (edge_volume_time['Volume'] > 0)].dropna()
all_FF_time = pd.merge(all_FF_time, edge_attr['Length'], left_on='Edge', right_index=True)
all_FF_time['FF_speed'] = all_FF_time['Length'] / all_FF_time['TravelTime'] / 1.467 # convert to miles per hour

Visualise free flow speed distribution given the above selection parameters

In [24]:
all_FF_time.loc[all_FF_time['FF_speed'] < 100., 'FF_speed'] \
.iplot(kind='histogram', bins=40, histnorm='percent',
       layout={'title': {'text': 'Free flow speed distribution histogram'},
               'xaxis': {'title': 'Speed (mph)'},
               'yaxis': {'title': 'Probability'}})

In [ ]:
# testing ffs distribution for same volume
Edge_vol_speed = pd.merge(edge_volume_time, edge_attr['Length'], left_on='Edge', right_index=True)
Edge_vol_speed['AvgSpeed'] = Edge_vol_speed['Length'] / Edge_vol_speed['TravelTime'] / 1.467 # convert to miles per hour
Edge_vol_speed = Edge_vol_speed[['Edge', 'Volume']]

Aggragate values for each edge

In [12]:
aggfunc=[np.mean, np.std]
edge_FF_pivot = all_FF_time.pivot_table(values=['TravelTime', 'Volume', 'FF_speed'], index=['Edge'],
                                        aggfunc={'TravelTime':aggfunc,
                                                 'Volume':aggfunc,
                                                 'FF_speed':aggfunc+['count']})
edge_FF_pivot.columns = [' '.join(col).strip() for col in edge_FF_pivot.columns.values]
edge_FF_pivot = edge_FF_pivot.rename(index=str, columns={'FF_speed count':'Valid data points'})

In [13]:
qgrid.show_grid(edge_FF_pivot, grid_options={'editable': False,'maxVisibleRows':10})

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…